This notebook aims to create a monthly view of the "experience" dataset, breaking job experiences that span across several months into individual months and the corresponding job experience.

# Import

In [1]:
import pandas as pd
import re

# pd.set_option('display.max_rows', 500)
# pd.set_option('display.max_columns', 500)

## 1) Experience by month

In [2]:
experience_df = pd.read_parquet('../data/processed/experience_df_with_model_classification.parquet')
experience_df['end_date'].replace({'Ongoing': '2024-05'}, inplace=True)
experience_df.head(3)

/tmp/ipykernel_73388/2822477393.py:2: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  experience_df['end_date'].replace({'Ongoing': '2024-05'}, inplace=True)


person_id  company_id start_date  end_date model_classification
0          0           0   Sep 2022   2024-05               131071
1          0           0   Jun 2018  Jan 2023               131111
2          0           1   May 2022   2024-05               000000

### Normalizing dates

In [3]:
def clean_string_column(terms_to_remove, replace_dict, df, col):
    """ Remove and/or replace some terms in a column, and also removes leading/trailing whitespaces."""

    def remove_terms(terms_to_remove, df, col):
        terms_to_remove_pattern = '|'.join(map(re.escape, terms_to_remove))
        df.loc[:, col] = df.loc[:, col].str.replace(terms_to_remove_pattern, '', regex=True)
        return df

    def replace_terms(replace_dict, df, col):
        df.loc[:, col] = df.loc[:, col].replace(replace_dict, regex=True)
        return df
    
    df = remove_terms(terms_to_remove, df, col)
    df = replace_terms(replace_dict, df, col)
    df.loc[:, col] = df.loc[:, col].str.lstrip()
    df.loc[:, col] = df.loc[:, col].str.rstrip()

    return df

In [4]:
dates_dict = {
    'jan. de': 'Jan',
    'fev. de': 'Feb',
    'mar. de': 'Mar',
    'abr. de': 'Apr',
    'mai. de': 'May',
    'jun. de': 'Jun',
    'jul. de': 'Jul',
    'ago. de': 'Aug',
    'set. de': 'Sep',
    'out. de': 'Oct',
    'nov. de': 'Nov',
    'dez. de': 'Dec'
}

terms_to_remove = []
experience_df = clean_string_column(terms_to_remove, dates_dict, experience_df, 'start_date')
experience_df = clean_string_column(terms_to_remove, dates_dict, experience_df, 'end_date')

In [ ]:
# Convert start_date and end_date to datetime objects
experience_df['start_date'] = pd.to_datetime(experience_df['start_date'], format='mixed', errors='coerce')
experience_df['end_date'] = pd.to_datetime(experience_df['end_date'], format='mixed', errors='coerce')
experience_df

person_id  company_id start_date   end_date model_classification
0              0           0 2022-09-01 2024-05-01               131071
1              0           0 2018-06-01 2023-01-01               131111
2              0           1 2022-05-01 2024-05-01               000000
3              0           2 2010-01-01 2024-05-01               030000
4              0           3 2010-01-01 2017-01-01               192041
...          ...         ...        ...        ...                  ...
35941       9244       10398 2019-09-01 2020-02-01               151252
35942       9244        3110 2019-07-01 2019-09-01               151211
35943       9244       10399 2018-04-01 2018-05-01               000000
35944       9245         652 2024-01-01 2024-05-01               132051
35945       9245        2574 2022-06-01 2023-11-01               000000

[35946 rows x 5 columns]

In [6]:
# DROPPING NaT rows
experience_df.dropna(subset=['start_date', 'end_date'], inplace=True)
experience_df.shape

(35839, 5)

In [7]:
single_experience_nodes_by_month_df = pd.DataFrame()

# Loop through rows and expand date range
for index, row in experience_df.iterrows():
    date_range = pd.date_range(start=row['start_date'], end=row['end_date'], freq='MS')
    temp_df = pd.DataFrame()
    
    # Copy all columns from the original DataFrame to the expanded DataFrame
    for col in experience_df.columns:
        temp_df[col] = [row[col]] * len(date_range)
    
    temp_df['date'] = date_range
    single_experience_nodes_by_month_df = pd.concat([single_experience_nodes_by_month_df, temp_df], ignore_index=True)

/tmp/ipykernel_73388/3704148251.py:13: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  single_experience_nodes_by_month_df = pd.concat([single_experience_nodes_by_month_df, temp_df], ignore_index=True)


In [8]:
single_experience_nodes_by_month_df = single_experience_nodes_by_month_df.sort_values(['person_id', 'date'], ascending=[True, False]).reset_index(drop=True)
single_experience_nodes_by_month_df

person_id  company_id start_date   end_date model_classification  \
0             0.0         0.0 2022-09-01 2024-05-01               131071   
1             0.0         1.0 2022-05-01 2024-05-01               000000   
2             0.0         2.0 2010-01-01 2024-05-01               030000   
3             0.0         0.0 2022-09-01 2024-05-01               131071   
4             0.0         1.0 2022-05-01 2024-05-01               000000   
...           ...         ...        ...        ...                  ...   
733057     9245.0      2574.0 2022-06-01 2023-11-01               000000   
733058     9245.0      2574.0 2022-06-01 2023-11-01               000000   
733059     9245.0      2574.0 2022-06-01 2023-11-01               000000   
733060     9245.0      2574.0 2022-06-01 2023-11-01               000000   
733061     9245.0      2574.0 2022-06-01 2023-11-01               000000   

             date  
0      2024-05-01  
1      2024-05-01  
2      2024-05-01  
3      2024-04-01  
4      2024-04-01  
...           ...  
733057 2022-10-01  
733058 2022-09-01  
733059 2022-08-01  
733060 2022-07-01  
733061 2022-06-01  

[733062 rows x 6 columns]

In [9]:
# single_experience_nodes_by_month_df.to_parquet('../data/processed/single_experience_nodes_by_month.parquet')

# experience_by_month_with_labels -> single_experience_nodes_by_month

## 2) Experience per month + periods with no job

In [10]:
def fill_gaps(group):
    # Generate a complete range of months from min to max for each person_id
    date_range = pd.date_range(group['date'].min(), group['date'].max(), freq='MS')
    
    # Create a new DataFrame to fill the gaps
    filled_group = pd.DataFrame(date_range, columns=['date'])
    
    # Map existing dates to job titles
    filled_group = filled_group.merge(group, on='date', how='left')
    
    # Fill missing job_titles with 'no job registered' and person_id with the group's person_id
    filled_group['model_classification'].fillna('no job registered', inplace=True)
    filled_group['person_id'] = group['person_id'].iloc[0]  # Assuming all rows have the same person_id
    
    return filled_group

# Apply the function to each person_id group and concatenate the results
single_experience_nodes_by_month_and_no_job_periods_df = pd.concat([fill_gaps(group) for _, group in single_experience_nodes_by_month_df.groupby('person_id')])
single_experience_nodes_by_month_and_no_job_periods_df

/tmp/ipykernel_73388/905721585.py:12: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  filled_group['model_classification'].fillna('no job registered', inplace=True)
/tmp/ipykernel_73388/905721585.py:12: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].me

date  person_id  company_id start_date   end_date  \
0  2010-01-01        0.0         2.0 2010-01-01 2024-05-01   
1  2010-01-01        0.0         3.0 2010-01-01 2017-01-01   
2  2010-02-01        0.0         2.0 2010-01-01 2024-05-01   
3  2010-02-01        0.0         3.0 2010-01-01 2017-01-01   
4  2010-03-01        0.0         2.0 2010-01-01 2024-05-01   
..        ...        ...         ...        ...        ...   
19 2024-01-01     9245.0       652.0 2024-01-01 2024-05-01   
20 2024-02-01     9245.0       652.0 2024-01-01 2024-05-01   
21 2024-03-01     9245.0       652.0 2024-01-01 2024-05-01   
22 2024-04-01     9245.0       652.0 2024-01-01 2024-05-01   
23 2024-05-01     9245.0       652.0 2024-01-01 2024-05-01   

   model_classification  
0                030000  
1                192041  
2                030000  
3                192041  
4                030000  
..                  ...  
19               132051  
20               132051  
21               132051  
22               132051  
23               132051  

[817075 rows x 6 columns]

In [11]:
single_experience_nodes_by_month_and_no_job_periods_df.to_parquet('../data/processed/single_experience_nodes_by_month_and_no_job_periods.parquet')